# Introduction

- Projet final présenté par: **François Pelletier**
- Matricule: **908144032**
- Dans le cadre du cours: **IFT-7025**

# Librairies utilisées

In [ ]:
import numpy as np
import load_datasets as ld
import matplotlib.pyplot as plt
import DecisionTree
import NeuralNet

## Iris Dataset

La présentation des résultats liés à ce jeu de données servira aussi à expliquer les concepts et répondre aux questions. Pour les autres jeux de données, seul les résultats et la discussion seront détaillés.

- Chargement du jeu de données

In [ ]:
train1, train_labels1, test1, test_labels1 = (
    ld.load_iris_dataset(train_ratio = 0.7))

### Entrainement de l'arbre de décision

Dans cette section, on entraine un arbre de décision basé sur la mesure d'entropie.

In [ ]:
dt1 = DecisionTree.DecisionTree(attribute_type="continuous")
_ = dt1.train(train1, train_labels1,verbose=False)

### Courbe d'apprentissage

Je trace une courbe d'apprentissage qui effectue une validation croisée sur 10 sous-ensembles de l'ensemble d'entrainement. Je vais la moyenne de l'accuracy pour chaque sous-ensemble de test, puis j'itère en ajoutant un exemple à la fois à l'ensemble d'entrainement.

- Bogue connu: J'ai débuté à courbe d'apprentissage avec 30 données car j'ai de la difficulté à exécuter la validation croisée avec moins sans que ça plante vu que je crée les sous-groupes à l'avance.

In [ ]:
def courbe_apprentissage_dt(dt,train,train_labels,nb_cv_split=10):
    accuracy_cum = []
    range_lc = range(30,len(train_labels))
    for i in range_lc:
        range_lc_split_test = np.array_split(range(i),nb_cv_split)
        range_lc_split_train = (
            [np.setdiff1d(range(i),t) for t in range_lc_split_test])
        accuracy_cv = []
        for r_i in range(nb_cv_split):
            try:
                training = dt.train(train[range_lc_split_train[r_i]], 
                                     train_labels[range_lc_split_train[r_i]],
                                     verbose=False)
                testres = dt.test(train[range_lc_split_test[r_i]], 
                                train_labels[range_lc_split_test[r_i]],
                                verbose=False)
                accuracy_cv.append(testres[1])
            except:
                pass
        accuracy_cum.append(np.mean(accuracy_cv))
    return range_lc,accuracy_cum

In [ ]:
range_lc1,accuracy_cum1 = courbe_apprentissage_dt(dt1,train1,train_labels1)

Voici le graphique de la courbe d'apprentissage

In [ ]:
plt.plot(range_lc1,accuracy_cum1)

### Test et évaluation de la performance de l'arbre de décision

In [ ]:
_ = dt1.test(test1, test_labels1)

### Réseaux de neurones: Choix du nombre de neurones dans la couche cachée

On doit identifier le nombre optimal de neurones dans la couche cachée dans l'intervalle $[4,50]$ pour chacun des 5 jeux de données. On itère sur chacun des jeux de validation croisée, pour chaque dimension et on calcule l'accuracy moyenne. La dimension qui a la meilleure accuracy moyenne est choisie pour construire le réseau de neurones.

In [ ]:
choix_n_neurones = range(4,51)

- Pour faire la séparation du jeu de données en $k_{cv}=5$ jeux de validation croisée, on génère une permutation sur les indices du jeu d'entrainement, puis, on sépare cet ensemble en 5 groupes.

In [ ]:
k_cv = 5
all_indices = range(len(train_labels1))
np.random.seed(12345)
indices_cv_test = (
    np.sort(np.array_split(np.random.permutation(all_indices),
                           k_cv)))

In [ ]:
indices_cv_train = (
    [np.setdiff1d(all_indices,indices_cv_test[i]) for i in range(k_cv)])

Ce jeux de données a trois classes possibles comme variable de sortie. On utilisera donc un réseau de neurones avec 3 neurones dans la couche de sortie, une pour chacune des valeurs possibles. Les valeurs de sortie du jeu de données sont transformées à l'aide d'un encodage binaire où la valeur de sortie est convertie en rang dans un vecteur (on commence à 0), prenant la valeur 1. Par exemple, la valeur 2 devient $[0,0,1]$.

In [ ]:
accuracy_cum = []
for n_neurones in choix_n_neurones:
    accuracy_cv=[]
    for cv_set in range(k_cv):
        nn1 = NeuralNet.NeuralNet(np.array([4,n_neurones,3]),range(3))
        nn1.train(train1[indices_cv_train[cv_set]], 
                  train_labels1[indices_cv_train[cv_set]], 0.1, 1, 
                  verbose=False)
        _,accuracy,_,_,_ = nn1.test(train1[indices_cv_test[cv_set]], 
                                    train_labels1[indices_cv_test[cv_set]], 
                                    verbose=False)
        accuracy_cv.append(accuracy)
    accuracy_cum.append(np.mean(np.array(accuracy_cv)))

In [ ]:
plt.plot(choix_n_neurones,accuracy_cum)

Le nombre de neurones qui maximise l'accuracy est de:

In [ ]:
n_neurones_optimal1 = (
    choix_n_neurones[np.where(accuracy_cum==max(accuracy_cum))[0][0]])
n_neurones_optimal1

### Choix du nombre de couches cachées

On choisit un nombre de 1 à 5 couches cachées. Le nombre de couche ayany l'accuracy maximale sera sélectionné pour la construction du réseau. On effectue 10 époques étant donné la taille des réseaux à entrainer.

In [ ]:
choix_n_couches = range(1,6)

In [ ]:
accuracy_cum = []
lc_cum = []
for n_couches in choix_n_couches:
    accuracy_cv=[]
    nn1 = NeuralNet.NeuralNet(
        np.hstack((4,
                   np.repeat(n_neurones_optimal1,n_couches),
                   3)),
        range(3))
    lc = nn1.train(train1, train_labels1, 0.1, 10, verbose=False)
    lc_cum.append(lc)
    _,accuracy,_,_,_ = nn1.test(train1, train_labels1, verbose=False)
    accuracy_cv.append(accuracy)
    accuracy_cum.append(np.mean(np.array(accuracy_cv)))
lc_cum = np.array(lc_cum)

L'accuracy pour les différentes profondeur est de :

In [ ]:
np.vstack((choix_n_couches,accuracy_cum))

Le nombre de couches cachées qui maximise l'accurary est de:

In [ ]:
n_couches_optimal1 = choix_n_couches[np.where(accuracy_cum==max(accuracy_cum))[0][0]]
n_couches_optimal1

Un problème rencontré avec un nombre de couches élevées est appelé le *Vanishing gradient problem*. Dans ces situaitons, le nombre de multiplications nécessaires ainsi que le fait que les valeurs $\Delta$ sont suffisamment petites pour que le gradient tende vers 0 et ainsi ne permette pas de mettre les poids à jour. Dans ces situations, l'entrainement va stagner.

### Courbes d'apprentissage

Ce graphique présente les courbes d'apprentissage pour chacun des niveaux de profondeur du réseau

In [ ]:
plt.subplot(111)
for i in choix_n_couches:
    plt.plot(range(10),lc_cum[i-1], label="%d couches"%(i,))
leg = plt.legend(loc='best', ncol=2, mode="expand", shadow=True, fancybox=True)
leg.get_frame().set_alpha(0.5)

### Choix des poids initiaux
Les poids initiaux ont été choisis à partir d'une distribution uniforme sur $[-1,1]$. On compare ici les courbes d'apprentissage en initialisant les poids à 0 et en initialisant les poids aléatoirement, pour le réseau de dimension et de profondeur optimale sélectionnées précédemment.

- Réseau initialisé avec les poids à 0 $RN_{0}$

In [ ]:
nn1_poidszero = NeuralNet.NeuralNet(
    np.hstack((4,
               np.repeat(n_neurones_optimal1,n_couches_optimal1),
               3)),
    range(3),
    input_weights=0)
lc_nn1_poidszero = (
    nn1_poidszero.train(train1, train_labels1, 0.1, 10, verbose=False))

- Réseau initialisé avec les poids uniformes $RN_{\neg{0}}$

In [ ]:
nn1_poidsunif = NeuralNet.NeuralNet(
    np.hstack((4,
               np.repeat(n_neurones_optimal1,n_couches_optimal1),
               3)),
    range(3))
np.random.seed(12345)
lc_nn1_poidsunif = (
    nn1_poidsunif.train(train1, train_labels1, 0.1, 10, verbose=False))

- Graphique des courbes d'apprentissage

In [ ]:
plt.subplot(111)
plt.plot(range(10),lc_nn1_poidszero, label="RN_Zero")
plt.plot(range(10),lc_nn1_poidsunif, label="RN_Non_Zero)")
leg = plt.legend(loc='best', 
                 ncol=2, 
                 mode="expand", 
                 shadow=True, 
                 fancybox=True)
leg.get_frame().set_alpha(0.5)

On remarque clairement que l'initialisation des poids à 0 ne permet pas de démarrer l'entrainement du réseau. Il est donc nécessaire d'initialiser les poids aléatoirement pour permettre l'apprentissage et éviter que les différentes fonctions pour calculer la rétropropagation des erreurs aient toutes des valeurs de 0.

### Entrainement et tests
On reprend les résultats du dernier entrainement, puisqu'il utilise les poids aléatoires et les hyperparamètres optimaux.

In [ ]:
_ = nn1_poidsunif.test(test1, test_labels1)

## MONKS Dataset

- Chargement des jeux de données

In [ ]:
train2, train_labels2, test2, test_labels2 = (
    ld.load_monks_dataset(1))
train3, train_labels3, test3, test_labels3 = (
    ld.load_monks_dataset(2))
train4, train_labels4, test4, test_labels4 = (
    ld.load_monks_dataset(3))

### Entrainement de l'arbre de décision

Dans cette section, on entraine un arbre de décision basé sur la mesure d'entropie.

In [ ]:
dt2 = DecisionTree.DecisionTree(attribute_type="discrete")
dt3 = DecisionTree.DecisionTree(attribute_type="discrete")
dt4 = DecisionTree.DecisionTree(attribute_type="discrete")

_ = dt2.train(train2, train_labels2,verbose=False)
_ = dt3.train(train3, train_labels3,verbose=False)
_ = dt4.train(train4, train_labels4,verbose=False)

### Courbe d'apprentissage

Je trace une courbe d'apprentissage qui effectue une validation croisée sur 10 sous-ensembles de l'ensemble d'entrainement. Je vais la moyenne de l'accuracy pour chaque sous-ensemble de test, puis j'itère en ajoutant un exemple à la fois à l'ensemble d'entrainement.

- Bogue connu: J'ai débuté à courbe d'apprentissage avec 30 données car j'ai de la difficulté à exécuter la validation croisée avec moins sans que ça plante vu que je crée les sous-groupes à l'avance.

In [ ]:
range_lc2,accuracy_cum2 = courbe_apprentissage_dt(dt2,train2,train_labels2)
range_lc3,accuracy_cum3 = courbe_apprentissage_dt(dt3,train3,train_labels3)
range_lc4,accuracy_cum4 = courbe_apprentissage_dt(dt4,train4,train_labels4)

Voici les graphiques de la courbe d'apprentissage pour les 3 jeux de données
- 1er jeu de données

In [ ]:
plt.plot(range_lc2,accuracy_cum2)

- 2e jeu de données

In [ ]:
plt.plot(range_lc3,accuracy_cum3)

- 3e jeu de données

In [ ]:
plt.plot(range_lc4,accuracy_cum4)

On peut facilement observer que dans les trois cas, il y a très peu d'apprentissage de réalisé par l'algorithme avec les exemples fournis.

### Test et évaluation de la performance de l'arbre de décision

In [ ]:
_ = dt2.test(test2, test_labels2)

In [ ]:
_ = dt3.test(test3, test_labels3)

In [ ]:
_ = dt4.test(test4, test_labels4)

### Réseaux de neurones: choix du nombre de neurones dans la couche cachée

- Pour faire la séparation du jeu de données en $k_{cv}=5$ jeux de validation croisée, on génère une permutation sur les indices du jeu d'entrainement, puis, on sépare cet ensemble en 5 groupes.

In [ ]:
all_indices2 = range(len(train_labels2))
all_indices3 = range(len(train_labels3))
all_indices4 = range(len(train_labels4))
np.random.seed(12345)
indices_cv_test2 = (
    [np.sort(x) for x in np.array_split(np.random.permutation(all_indices2),k_cv)])
np.random.seed(12345)
indices_cv_test3 = (
    [np.sort(x) for x in np.array_split(np.random.permutation(all_indices3),k_cv)])
np.random.seed(12345)
indices_cv_test4 = (
    [np.sort(x) for x in np.array_split(np.random.permutation(all_indices4),k_cv)])

In [ ]:
indices_cv_train2 = (
    [np.setdiff1d(all_indices,indices_cv_test2[i]) for i in range(k_cv)])
indices_cv_train3 = (
    [np.setdiff1d(all_indices,indices_cv_test3[i]) for i in range(k_cv)])
indices_cv_train4 = (
    [np.setdiff1d(all_indices,indices_cv_test4[i]) for i in range(k_cv)])

Ces jeux de données ont deux classes possibles comme variable de sortie. On utilisera donc un réseau de neurones avec deux neurone dans la couche de sortie, une pour chacune des valeurs possibles. Les valeurs de sortie du jeu de données sont transformées à l'aide d'un encodage binaire où la valeur de sortie est convertie en rang dans un vecteur (on commence à 0), prenant la valeur 1. Par exemple, la valeur 1 devient $[0,1]$.

In [ ]:
accuracy_cum2 = []
for n_neurones in choix_n_neurones:
    accuracy_cv=[]
    for cv_set in range(k_cv):
        nn2 = NeuralNet.NeuralNet(np.array([6,n_neurones,2]),range(2))
        nn2.train(train2[indices_cv_train2[cv_set]], 
                  train_labels2[indices_cv_train2[cv_set]], 0.1, 1, 
                  verbose=False)
        _,accuracy,_,_,_ = nn2.test(train2[indices_cv_test2[cv_set]], 
                                    train_labels2[indices_cv_test2[cv_set]], 
                                    verbose=False)
        accuracy_cv.append(accuracy)
    accuracy_cum2.append(np.mean(np.array(accuracy_cv)))

In [ ]:
plt.plot(choix_n_neurones,accuracy_cum2)

Le nombre de neurones qui maximise l'accuracy est de:

In [ ]:
n_neurones_optimal2 = (
    choix_n_neurones[np.where(accuracy_cum2==max(accuracy_cum2))[0][0]])
n_neurones_optimal2

In [ ]:
accuracy_cum3 = []
for n_neurones in choix_n_neurones:
    accuracy_cv=[]
    for cv_set in range(k_cv):
        nn3 = NeuralNet.NeuralNet(np.array([6,n_neurones,2]),range(2))
        nn3.train(train3[indices_cv_train3[cv_set]], 
                  train_labels3[indices_cv_train3[cv_set]], 0.1, 1, 
                  verbose=False)
        _,accuracy,_,_,_ = nn3.test(train3[indices_cv_test3[cv_set]], 
                                    train_labels3[indices_cv_test3[cv_set]], 
                                    verbose=False)
        accuracy_cv.append(accuracy)
    accuracy_cum3.append(np.mean(np.array(accuracy_cv)))

In [ ]:
plt.plot(choix_n_neurones,accuracy_cum3)

Le nombre de neurones qui maximise l'accuracy est de:

In [ ]:
n_neurones_optimal3 = (
    choix_n_neurones[np.where(accuracy_cum3==max(accuracy_cum3))[0][0]])
n_neurones_optimal3

In [ ]:
accuracy_cum4 = []
for n_neurones in choix_n_neurones:
    accuracy_cv=[]
    for cv_set in range(k_cv):
        nn4 = NeuralNet.NeuralNet(np.array([6,n_neurones,2]),range(2))
        nn4.train(train4[indices_cv_train4[cv_set]], 
                  train_labels4[indices_cv_train4[cv_set]], 0.1, 1, 
                  verbose=False)
        _,accuracy,_,_,_ = nn4.test(train4[indices_cv_test4[cv_set]], 
                                    train_labels4[indices_cv_test4[cv_set]], 
                                    verbose=False)
        accuracy_cv.append(accuracy)
    accuracy_cum4.append(np.mean(np.array(accuracy_cv)))

In [ ]:
plt.plot(choix_n_neurones,accuracy_cum4)

Le nombre de neurones qui maximise l'accuracy est de:

In [ ]:
n_neurones_optimal4 = (
    choix_n_neurones[np.where(accuracy_cum4==max(accuracy_cum4))[0][0]])
n_neurones_optimal4

### Choix du nombre de couches cachées

On choisit un nombre de 1 à 5 couches cachées. Le nombre de couche ayany l'accuracy maximale sera sélectionné pour la construction du réseau. On effectue 10 époques étant donné la taille des réseaux à entrainer.

In [ ]:
def accuracy_couches(train,train_labels,n_neurones_optimal):
    accuracy_cum = []
    lc_cum = []
    for n_couches in choix_n_couches:
        accuracy_cv=[]
        nn = NeuralNet.NeuralNet(
            np.hstack((6,
                       np.repeat(n_neurones_optimal,n_couches),
                       2)),
            range(2))
        lc = nn.train(train, train_labels, 0.1, 10, verbose=False)
        lc_cum.append(lc)
        _,accuracy,_,_,_ = nn.test(train, train_labels, verbose=False)
        accuracy_cv.append(accuracy)
        accuracy_cum.append(np.mean(np.array(accuracy_cv)))
    lc_cum = np.array(lc_cum)
    return accuracy_cum, lc_cum

In [ ]:
accuracy_cum2, lc_cum2 = accuracy_couches(train2,train_labels2,n_neurones_optimal2)
accuracy_cum3, lc_cum3 = accuracy_couches(train3,train_labels3,n_neurones_optimal3)
accuracy_cum4, lc_cum4 = accuracy_couches(train4,train_labels4,n_neurones_optimal4)

L'accuracy pour les différentes profondeur est respectivement (un jeu de données par ligne) de :

In [ ]:
np.vstack((choix_n_couches,accuracy_cum2,accuracy_cum3,accuracy_cum4))

Le nombre de couches cachées qui maximise l'accurary est, pour chacun des 3 jeux de données, respectivement de:

In [ ]:
n_couches_optimal2 = choix_n_couches[np.where(accuracy_cum2==max(accuracy_cum2))[0][0]]
n_couches_optimal3 = choix_n_couches[np.where(accuracy_cum3==max(accuracy_cum3))[0][0]]
n_couches_optimal4 = choix_n_couches[np.where(accuracy_cum4==max(accuracy_cum4))[0][0]]
(n_couches_optimal2,n_couches_optimal3,n_couches_optimal4)

### Courbes d'apprentissage

Ce graphique présente les courbes d'apprentissage pour chacun des niveaux de profondeur du réseau

In [ ]:
plt.subplot(111)
for i in choix_n_couches:
    plt.plot(range(10),lc_cum2[i-1], label="%d couches"%(i,))
leg = plt.legend(loc='best', ncol=2, mode="expand", shadow=True, fancybox=True)
leg.get_frame().set_alpha(0.5)

In [ ]:
plt.subplot(111)
for i in choix_n_couches:
    plt.plot(range(10),lc_cum3[i-1], label="%d couches"%(i,))
leg = plt.legend(loc='best', ncol=2, mode="expand", shadow=True, fancybox=True)
leg.get_frame().set_alpha(0.5)

In [ ]:
plt.subplot(111)
for i in choix_n_couches:
    plt.plot(range(10),lc_cum4[i-1], label="%d couches"%(i,))
leg = plt.legend(loc='best', ncol=2, mode="expand", shadow=True, fancybox=True)
leg.get_frame().set_alpha(0.5)

### Choix des poids initiaux
Les poids initiaux ont été choisis à partir d'une distribution uniforme sur $[-1,1]$. On compare ici les courbes d'apprentissage en initialisant les poids à 0 et en initialisant les poids aléatoirement, pour le réseau de dimension et de profondeur optimale sélectionnées précédemment.

- Réseau initialisé avec les poids à 0 $RN_{0}$

In [ ]:
nn2_poidszero = NeuralNet.NeuralNet(
    np.hstack((6,
               np.repeat(n_neurones_optimal2,n_couches_optimal2),
               2)),
    range(2),
    input_weights=0)
lc_nn2_poidszero = (
    nn2_poidszero.train(train2, train_labels2, 0.1, 10, verbose=False))

In [ ]:
nn3_poidszero = NeuralNet.NeuralNet(
    np.hstack((6,
               np.repeat(n_neurones_optimal3,n_couches_optimal3),
               2)),
    range(2),
    input_weights=0)
lc_nn3_poidszero = (
    nn3_poidszero.train(train3, train_labels3, 0.1, 10, verbose=False))

In [ ]:
nn4_poidszero = NeuralNet.NeuralNet(
    np.hstack((6,
               np.repeat(n_neurones_optimal4,n_couches_optimal4),
               2)),
    range(2),
    input_weights=0)
lc_nn4_poidszero = (
    nn4_poidszero.train(train4, train_labels4, 0.1, 10, verbose=False))

- Réseau initialisé avec les poids uniformes $RN_{\neg{0}}$

In [ ]:
nn2_poidsunif = NeuralNet.NeuralNet(
    np.hstack((6,
               np.repeat(n_neurones_optimal2,n_couches_optimal2),
               2)),
    range(2))
np.random.seed(12345)
lc_nn2_poidsunif = (
    nn2_poidsunif.train(train2, train_labels2, 0.1, 10, verbose=False))

In [ ]:
nn3_poidsunif = NeuralNet.NeuralNet(
    np.hstack((6,
               np.repeat(n_neurones_optimal3,n_couches_optimal3),
               2)),
    range(2))
np.random.seed(12345)
lc_nn3_poidsunif = (
    nn3_poidsunif.train(train3, train_labels3, 0.1, 10, verbose=False))

In [ ]:
nn4_poidsunif = NeuralNet.NeuralNet(
    np.hstack((6,
               np.repeat(n_neurones_optimal4,n_couches_optimal4),
               2)),
    range(2))
np.random.seed(12345)
lc_nn4_poidsunif = (
    nn4_poidsunif.train(train4, train_labels4, 0.1, 10, verbose=False))

- Graphique des courbes d'apprentissage

- MONKS1

In [ ]:
plt.subplot(111)
plt.plot(range(10),lc_nn2_poidszero, label="MONKS1: RN_Zero")
plt.plot(range(10),lc_nn2_poidsunif, label="MONKS1: RN_Non_Zero)")
leg = plt.legend(loc='best', 
                 ncol=2, 
                 mode="expand", 
                 shadow=True, 
                 fancybox=True)
leg.get_frame().set_alpha(0.5)

- MONKS2

In [ ]:
plt.subplot(111)
plt.plot(range(10),lc_nn3_poidszero, label="MONKS2: RN_Zero")
plt.plot(range(10),lc_nn3_poidsunif, label="MONKS2: RN_Non_Zero)")
leg = plt.legend(loc='best', 
                 ncol=2, 
                 mode="expand", 
                 shadow=True, 
                 fancybox=True)
leg.get_frame().set_alpha(0.5)

- MONKS3

In [ ]:
plt.subplot(111)
plt.plot(range(10),lc_nn4_poidszero, label="MONKS3: RN_Zero")
plt.plot(range(10),lc_nn4_poidsunif, label="MONKS3: RN_Non_Zero)")
leg = plt.legend(loc='best', 
                 ncol=2, 
                 mode="expand", 
                 shadow=True, 
                 fancybox=True)
leg.get_frame().set_alpha(0.5)

On remarque ici aussi que l'initialisation des poids à 0 ne permet pas de démarrer l'entrainement du réseau. Dans le second jeu de données, cependant, l'initialisation aléatoire ne permet pas non plus de démarrer l'apprentissage.

### Entrainement et tests
On reprend les résultats du dernier entrainement, puisqu'il utilise les poids aléatoires et les hyperparamètres optimaux.

In [ ]:
_ = nn2_poidsunif.test(test2, test_labels2)

In [ ]:
_ = nn3_poidsunif.test(test3, test_labels3)

In [ ]:
_ = nn4_poidsunif.test(test4, test_labels4)

## Congressionnal Dataset

- Chargement du jeu de données

In [ ]:
train5, train_labels5, test5, test_labels5 = (
    ld.load_congressional_dataset(train_ratio = 0.7))

### Entrainement de l'arbre de décision

Dans cette section, on entraine un arbre de décision basé sur la mesure d'entropie.

In [ ]:
dt5 = DecisionTree.DecisionTree(attribute_type="discrete")
_ = dt5.train(train5, train_labels5, verbose=False)

### Courbe d'apprentissage

In [ ]:
range_lc5,accuracy_cum5 = courbe_apprentissage_dt(dt5,train5,train_labels5)

Voici le graphique de la courbe d'apprentissage

In [ ]:
plt.plot(range_lc5,accuracy_cum5)

### Test et évaluation de la performance de l'arbre de décision

In [ ]:
_ = dt5.test(test5, test_labels5)

### Réseaux de neurones: Choix du nombre de neurones dans la couche cachée

- Pour faire la séparation du jeu de données en $k_{cv}=5$ jeux de validation croisée, on génère une permutation sur les indices du jeu d'entrainement, puis, on sépare cet ensemble en 5 groupes.

In [ ]:
all_indices5 = range(len(train_labels5))
np.random.seed(12345)
indices_cv_test5 = (
    [np.sort(x) for x in (np.array_split(np.random.permutation(all_indices5),
                           k_cv))])

In [ ]:
indices_cv_train5 = (
    [np.setdiff1d(all_indices5,indices_cv_test5[i]) for i in range(k_cv)])

Ce jeux de données a trois classes possibles comme variable de sortie. On utilisera donc un réseau de neurones avec 3 neurones dans la couche de sortie, une pour chacune des valeurs possibles. Les valeurs de sortie du jeu de données sont transformées à l'aide d'un encodage binaire où la valeur de sortie est convertie en rang dans un vecteur (on commence à 0), prenant la valeur 1. Par exemple, la valeur 2 devient $[0,0,1]$.

In [ ]:
accuracy_cum5 = []
for n_neurones in choix_n_neurones:
    accuracy_cv=[]
    for cv_set in range(k_cv):
        accuracy=0
        try:
            nn5 = NeuralNet.NeuralNet(np.array([16,n_neurones,3]),range(3))
            nn5.train(train5[indices_cv_train5[cv_set]], 
                      train_labels5[indices_cv_train5[cv_set]], 0.1, 1, 
                      verbose=False)
            _,accuracy,_,_,_ = nn5.test(train5[indices_cv_test5[cv_set]], 
                                        train_labels5[indices_cv_test5[cv_set]], 
                                        verbose=False)
        except:
            pass
        accuracy_cv.append(accuracy)
    accuracy_cum5.append(np.mean(np.array(accuracy_cv)))

In [ ]:
plt.plot(choix_n_neurones,accuracy_cum5)

Le nombre de neurones qui maximise l'accuracy est de:

In [ ]:
n_neurones_optimal5 = (
    choix_n_neurones[np.where(accuracy_cum5==max(accuracy_cum5))[0][0]])
n_neurones_optimal5

### Choix du nombre de couches cachées

On choisit un nombre de 1 à 5 couches cachées. Le nombre de couche ayany l'accuracy maximale sera sélectionné pour la construction du réseau. On effectue 10 époques étant donné la taille des réseaux à entrainer.

In [ ]:
accuracy_cum5 = []
lc_cum5 = []
for n_couches in choix_n_couches:
    accuracy_cv=[]
    nn5 = NeuralNet.NeuralNet(
        np.hstack((16,
                   np.repeat(n_neurones_optimal5,n_couches),
                   3)),
        range(3))
    lc = nn5.train(train5, train_labels5, 0.1, 10, verbose=False)
    lc_cum5.append(lc)
    _,accuracy,_,_,_ = nn5.test(train5, train_labels5, verbose=False)
    accuracy_cv.append(accuracy)
    accuracy_cum5.append(np.mean(np.array(accuracy_cv)))
lc_cum5 = np.array(lc_cum5)

L'accuracy pour les différentes profondeur est de :

In [ ]:
np.vstack((choix_n_couches,accuracy_cum5))

Le nombre de couches cachées qui maximise l'accurary est de:

In [ ]:
n_couches_optimal5 = choix_n_couches[np.where(accuracy_cum5==max(accuracy_cum5))[0][0]]
n_couches_optimal5

Un problème rencontré avec un nombre de couches élevées est appelé le *Vanishing gradient problem*. Dans ces situaitons, le nombre de multiplications nécessaires ainsi que le fait que les valeurs $\Delta$ sont suffisamment petites pour que le gradient tende vers 0 et ainsi ne permette pas de mettre les poids à jour. Dans ces situations, l'entrainement va stagner.

### Courbes d'apprentissage

Ce graphique présente les courbes d'apprentissage pour chacun des niveaux de profondeur du réseau

In [ ]:
plt.subplot(111)
for i in choix_n_couches:
    plt.plot(range(10),lc_cum5[i-1], label="%d couches"%(i,))
leg = plt.legend(loc='best', ncol=2, mode="expand", shadow=True, fancybox=True)
leg.get_frame().set_alpha(0.5)

### Choix des poids initiaux
Les poids initiaux ont été choisis à partir d'une distribution uniforme sur $[-1,1]$. On compare ici les courbes d'apprentissage en initialisant les poids à 0 et en initialisant les poids aléatoirement, pour le réseau de dimension et de profondeur optimale sélectionnées précédemment.

- Réseau initialisé avec les poids à 0 $RN_{0}$

In [ ]:
nn5_poidszero = NeuralNet.NeuralNet(
    np.hstack((16,
               np.repeat(n_neurones_optimal5,n_couches_optimal5),
               3)),
    range(3),
    input_weights=0)
lc_nn5_poidszero = (
    nn5_poidszero.train(train5, train_labels5, 0.1, 10, verbose=False))

- Réseau initialisé avec les poids uniformes $RN_{\neg{0}}$

In [ ]:
nn5_poidsunif = NeuralNet.NeuralNet(
    np.hstack((16,
               np.repeat(n_neurones_optimal5,n_couches_optimal5),
               3)),
    range(3))
np.random.seed(12345)
lc_nn5_poidsunif = (
    nn5_poidsunif.train(train5, train_labels5, 0.1, 10, verbose=False))

- Graphique des courbes d'apprentissage

In [ ]:
plt.subplot(111)
plt.plot(range(10),lc_nn5_poidszero, label="RN_Zero")
plt.plot(range(10),lc_nn5_poidsunif, label="RN_Non_Zero)")
leg = plt.legend(loc='best', 
                 ncol=2, 
                 mode="expand", 
                 shadow=True, 
                 fancybox=True)
leg.get_frame().set_alpha(0.5)

On remarque ici aussi que l'initialisation des poids à 0 ne permet pas de démarrer l'entrainement du réseau.

### Entrainement et tests
On reprend les résultats du dernier entrainement, puisqu'il utilise les poids aléatoires et les hyperparamètres optimaux.

In [ ]:
_ = nn5_poidsunif.test(test5, test_labels5)